In [6]:
import scipy.io
import numpy as np
from random import shuffle
import random
import scipy.ndimage
from skimage.util import pad
import os
import time
import pandas as pd
import math

In [9]:
patch_size = 9

## Load data
DATA_PATH = os.path.join(os.getcwd(), "Data")
Data = scipy.io.loadmat(os.path.join(DATA_PATH, 'Indian_pines.mat'))['indian_pines']
Label = scipy.io.loadmat(os.path.join(DATA_PATH, 'Indian_pines_gt.mat'))['indian_pines_gt']

## Some constant parameters
Height, Width, Band = Data.shape[0], Data.shape[1], Data.shape[2]
Num_Classes = len(np.unique(Label)) - 1  # Simu: len(np.unique(Label))

## Scale the HSI Data between [0,1]
Data = Data.astype(float)
for band in range(Band):
    Data[:, :, band] = (Data[:, :, band] - np.min(Data[:, :, band])) / (
            np.max(Data[:, :, band]) - np.min(Data[:, :, band]))

## padding the data beforehand
Height, Width, Band = Data.shape[0], Data.shape[1], Data.shape[2]
Data_Padding = np.zeros((Height + int(patch_size - 1), Width + int(patch_size - 1), Band))
for band in range(Band):
    Data_Padding[:, :, band] = pad(Data[:, :, band], int((patch_size - 1) / 2), 'symmetric')



In [10]:
def Patch(height_index, width_index):
    """ function to extract patches from the orignal data """
    transpose_array = np.transpose(Data_Padding, (2, 0, 1))
    height_slice = slice(height_index, height_index + patch_size)
    width_slice = slice(width_index, width_index + patch_size)
    patch = transpose_array[:, height_slice, width_slice]
    return np.array(patch)


In [12]:
## Collect patches for each class
Classes, Classes_Index = [], []
for k in range(Num_Classes):
    Classes.append([])
    Classes_Index.append([])

All_Patches, All_Labels = [], []
for j in range(0, Width):
    for i in range(0, Height):
        curr_inp = Patch(i, j)
        curr_ind = j * Height + i
        curr_tar = Label[i, j]
        All_Patches.append(curr_inp)
        All_Labels.append(curr_tar)
        # Ignore patches with unknown landcover type for the central pixel
        if (curr_tar != 0):
            Classes[curr_tar - 1].append(curr_inp)
            Classes_Index[curr_tar - 1].append(curr_ind)
All_data = {}
All_data['patch'] = All_Patches
All_data['labels'] = All_Labels
Data = None
Label = None
Num_Each_Class = []
for k in range(Num_Classes):
    Num_Each_Class.append(len(Classes[k]))


TypeError: 'NoneType' object is not subscriptable

In [13]:
def DataDivide(Classes_k, Num_Train_Each_Class_k, Classes_Index_k):
    """ function to divide collected patches into training and test patches """
    np.random.seed(0)
    idx = np.random.choice(len(Classes_k), Num_Train_Each_Class_k, replace=False)
    train_patch = [Classes_k[i] for i in idx]
    train_index = [Classes_Index_k[i] for i in idx]
    idx_test = np.setdiff1d(range(len(Classes_k)), idx)
    test_patch = [Classes_k[i] for i in idx_test]
    test_index = [Classes_Index_k[i] for i in idx_test]
    return train_patch, test_patch, train_index, test_index


In [14]:
## Make a train and test split 
# method 1: fixed proportion
train_frac = 0.05
Num_Train_Each_Class = [math.ceil(train_frac * x) for x in Num_Each_Class]
Num_Train_Each_Class = [int(x) for x in Num_Train_Each_Class]

Num_Test_Each_Class = list(np.array(Num_Each_Class) - np.array(Num_Train_Each_Class))
Train_Patch, Train_Label, Test_Patch, Test_Label = [], [], [], []
TestIndex, TrainIndex = [], []

In [15]:
import pickle as pkl
with open("Data/All_data.")

{'patch': [array([[[0.30769231, 0.0055668 , 0.00506073, ..., 0.0055668 ,
           0.30769231, 0.30769231],
          [0.00809717, 0.09311741, 0.00809717, ..., 0.09311741,
           0.00809717, 0.09311741],
          [0.56983806, 0.09615385, 0.09463563, ..., 0.09615385,
           0.56983806, 0.09311741],
          ...,
          [0.00809717, 0.09311741, 0.00809717, ..., 0.09311741,
           0.00809717, 0.09311741],
          [0.30769231, 0.0055668 , 0.00506073, ..., 0.0055668 ,
           0.30769231, 0.30769231],
          [0.00860324, 0.09261134, 0.65536437, ..., 0.09261134,
           0.00860324, 0.56882591]],
  
         [[0.51202636, 0.51334432, 0.43163097, ..., 0.51334432,
           0.51202636, 0.47116969],
          [0.59308072, 0.51532125, 0.55354201, ..., 0.51532125,
           0.59308072, 0.47215815],
          [0.55189456, 0.51367381, 0.51235585, ..., 0.51367381,
           0.55189456, 0.47051071],
          ...,
          [0.59308072, 0.51532125, 0.55354201, ..., 0.515